# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model loaded [MaskablePPO]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 399, done.
remote: Counting objects: 100% (6/6), done.
remote: Compressing objects: 100% (6/6), done.
remote: Total 399 (delta 0), reused 2 (delta 0), pack-reused 393
Receiving objects: 100% (399/399), 151.25 MiB | 20.79 MiB/s, done.
Resolving deltas: 100% (149/149), done.
Checking out files: 100% (108/108), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          README.md             VPP_environment.py
data/                             Simulator_notebooks/  VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  trained_models/       wandb/


In [3]:
import yaml
import numpy as np
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import MaskablePPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env
from sb3_contrib.common.maskable.evaluation import evaluate_policy

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')
wandb, version 0.13.4


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f63b615f5d0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  20171.87 , over-consume=kWh  37615.48 , under-consume=kWh  17443.61 , Total_cost=€  816.38 , overcost=€  1320.0 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
%env "WANDB_DISABLE_CODE" True
%env "WANDB_NOTEBOOK_NAME" "Simulator_notebooks/MaskablePPO_VPP_simulator.ipynb"
os.environ['WANDB_NOTEBOOK_NAME'] = 'Simulator_notebooks/MaskablePPO_VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

env: "WANDB_DISABLE_CODE"=True
env: "WANDB_NOTEBOOK_NAME"="Simulator_notebooks/MaskablePPO_VPP_simulator.ipynb"


In [21]:
#Loading training model, from local directory or from wandb previous trainings
MaskablePPO_path = "trained_models/MaskablePPO_models/model_MaskablePPO_"

model_id = "8mq440dz"
model = MaskablePPO.load(MaskablePPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, action_masks=action_masks, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21975.48 , over-consume=kWh  39575.82 , under-consume=kWh  17600.34 , Total_cost=€  921.95 , overcost=€  1425.06 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -10590.49 , over-consume=KWh  1788.37 , under-consume=KWh  12378.86 , Total_cost=€  -256.4 , Overcost=€  64.19 
 EV_INFO: Av.EV_energy_leaving=kWh  59.57 , Std.EV_energy_leaving=kWh  22.44 , EV_departures =  1043 , EV_queue_left =  0
SCORE:  Cumulative_reward= 222671.94 - Step_rewars (load_t= 229238.3, EVs_energy_t= -12806.58)
 - Final_rewards (EVs_energy= 5264.69, Overconsume= -1028.1, Underconsume= -9437.45, Overcost= 11441.08)
Episode:1 Score:222671.93953216783


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000  59.020191  47.426800   
2022-01-01 00:15:00   0.000000   0.000000  59.020191  47.426800   
2022-01-01 00:30:00   0.000000   0.000000  59.020191  46.832565   
2022-01-01 00:45:00   0.000000   0.000000  59.020191  46.410061   
2022-01-01 01:00:00   0.000000   0.000000  59.020191  46.073437   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  99.527588  55.555283  81.821251  54.772221   
2022-06-06 05:00:00  99.989998  55.305283  83.334007  54.772221   
2022-06-06 05:15:00  99.989998  55.055283  84.938133  54.772221   
2022-06-06 05:30:00  99.989998  54.805283  86.574409  54.772221   
2022-06-06 05:45:00  99.989998  54.555283  88.213707  54.772221   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 0, 0, 0]   
2022-01-01 00:15:00        [0, 0, 3128, 3129]  [0, 0, 0, 2]   
2022-01-01 00:30:00        [0, 0, 3128, 3129]  [0, 0, 0, 2]   
2022-01-01 00:45:00        [0, 0, 3128, 3129]  [0, 0, 0, 2]   
2022-01-01 01:00:00        [0, 0, 3128, 3129]  [0, 0, 0, 2]   
...                                       ...           ...   
2022-06-06 04:45:00  [3595, 3593, 3594, 3596]  [1, 2, 1, 0]   
2022-06-06 05:00:00  [3595, 3593, 3594, 3596]  [1, 2, 1, 0]   
2022-06-06 05:15:00  [3595, 3593, 3594, 3596]  [1, 2, 1, 0]   
2022-06-06 05:30:00  [3595, 3593, 3594, 3596]  [1, 2, 1, 0]   
2022-06-06 05:45:00  [3595, 3593, 3594, 3596]  [0, 2, 1, 0]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00    [False, True, True, True]        0.000000   
2022-01-01 00:15:00    [True, True, False, True]        0.000000   
2022-01-01 00:30:00    [True, True, False, True]        0.000000   
2022-01-01 00:45:00    [True, True, False, True]        0.000000   
2022-01-01 01:00:00    [True, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00  [False, False, True, False]        8.540582   
2022-06-06 05:00:00  [False, False, True, False]        7.900661   
2022-06-06 05:15:00  [False, False, True, False]        6.416520   
2022-06-06 05:30:00  [False, False, True, False]        6.545117   
2022-06-06 05:45:00    [True, False, True, True]        6.557210   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  2.868128e+00    -4.162224        0.0   
2022-01-01 00:15:00           0.000000  2.997334e+00    15.000000        0.0   
2022-01-01 00:30:00          -2.376939  0.000000e+00    15.000000        0.0   
2022-01-01 00:45:00          -1.690010  0.000000e+00    15.000000        0.0   
2022-01-01 01:00:00          -1.346490  0.000000e+00    10.620685        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00          -1.000000  8.881784e-16    -5.183058        0.0   
2022-06-06 05:00:00          -1.000000 -4.201364e+00    -7.196821        0.0   
2022-06-06 05:15:00          -1.000000 -6.416503e+00    -7.313727        0.0   
2022-06-06 05:30:00          -1.000000 -6.545100e+00    -7.324720        0.0   
2022-06-06 05:45:00          -1.000000 -6.557192e+00    -3.329531        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -4.162224  
2022-01-01 00:15:00  15.000000  
2022-01-01 00:30:00  15.000000  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  10.620685  
...                        ...  
2022-06-06 04:45:00  -5.183058  
2022-06-06 05:00:00  -7.196821  
2022-06-06 05:15:00  -7.313727  
2022-06-06 05:30:00  -7.324720  
2022-06-06 05:4

In [25]:
#env.plot_Elvis_results()

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [28]:
env.plot_VPP_Elvis_comparison()

In [29]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [30]:
env.plot_rewards_stats()

In [31]:
env.plot_EVs_kpi()

In [32]:
env.plot_load_kpi()

In [33]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [34]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 00:30:00, Parking_time: 24, Leaving_time: 2022-01-02 00:30:00, SOC: 0.4671232162245333, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-31 20:15:00, Parking_time: 23.765283451593486, Leaving_time: 2023-01-01 20:00:55.020426, SOC: 0.47397309298265095, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13077.16 , over-consume=kWh  34785.48 , under-consume=kWh  21708.32 , Total_cost=€  614.19 , overcost=€  1504.19 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [35]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [36]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = MaskablePPO.load(MaskablePPO_path + model_id, env=env)

In [37]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, action_masks=action_masks, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13027.85 , over-consume=kWh  34775.16 , under-consume=kWh  21747.32 , Total_cost=€  665.55 , overcost=€  1544.83 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -13989.02 , over-consume=KWh  1112.55 , under-consume=KWh  15101.57 , Total_cost=€  -541.84 , Overcost=€  48.02 
 EV_INFO: Av.EV_energy_leaving=kWh  65.46 , Std.EV_energy_leaving=kWh  22.22 , EV_departures =  1040 , EV_queue_left =  0
SCORE:  Cumulative_reward= 234570.77 - Step_rewars (load_t= 211790.25, EVs_energy_t= 8423.59)
 - Final_rewards (EVs_energy= 10022.04, Overconsume= -489.5, Underconsume= -9270.2, Overcost= 14094.59)
Episode:1 Score:234570.7703468


In [38]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [39]:
VPP_table.head(15000)

0    1          2          3  \
time                                                        
2022-01-01 00:00:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:15:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:30:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:45:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 01:00:00   0.000000  0.0   0.000000   0.000000   
...                        ...  ...        ...        ...   
2022-06-06 04:45:00  85.885246  0.0  70.865715  53.173809   
2022-06-06 05:00:00  87.040207  0.0  72.020676  53.173809   
2022-06-06 05:15:00  88.298515  0.0  73.278984  53.173809   
2022-06-06 05:30:00  89.484222  0.0  74.464691  53.173809   
2022-06-06 05:45:00  90.652367  0.0  75.632835  53.173809   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 00:15:00           [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 00:30:00           [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 00:45:00           [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 01:00:00           [0, 0, 0, 0]  [0, 0, 0, 0]   
...                                    ...           ...   
2022-06-06 04:45:00  [6679, 0, 6681, 6680]  [1, 1, 1, 0]   
2022-06-06 05:00:00  [6679, 0, 6681, 6680]  [1, 1, 1, 0]   
2022-06-06 05:15:00  [6679, 0, 6681, 6680]  [1, 1, 1, 0]   
2022-06-06 05:30:00  [6679, 0, 6681, 6680]  [1, 1, 1, 0]   
2022-06-06 05:45:00  [6679, 0, 6681, 6680]  [1, 1, 1, 0]   

                                     mask_truth  ev_charged_pwr  \
time                                                              
2022-01-01 00:00:00    [True, True, True, True]        0.000000   
2022-01-01 00:15:00    [True, True, True, True]        0.000000   
2022-01-01 00:30:00    [True, True, True, True]        0.000000   
2022-01-01 00:45:00    [True, True, True, True]        0.000000   
2022-01-01 01:00:00    [True, True, True, True]        0.000000   
...                                         ...             ...   
2022-06-06 04:45:00  [True, False, True, False]        7.172147   
2022-06-06 05:00:00  [True, False, True, False]        9.239655   
2022-06-06 05:15:00  [True, False, True, False]       10.066495   
2022-06-06 05:30:00  [True, False, True, False]        9.485639   
2022-06-06 05:45:00  [True, False, True, False]        9.345178   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -2.702976    -5.614021        0.0   
2022-01-01 00:15:00                0.0 -4.675423    -3.583872        0.0   
2022-01-01 00:30:00                0.0 -3.150323    -4.900382        0.0   
2022-01-01 00:45:00                0.0 -3.940229    -5.754368        0.0   
2022-01-01 01:00:00                0.0 -4.829805    -5.033976        0.0   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00                0.0 -3.586074    -5.563480        0.0   
2022-06-06 05:00:00                0.0 -4.619828    -5.939316        0.0   
2022-06-06 05:15:00                0.0 -5.033248    -5.675291        0.0   
2022-06-06 05:30:00                0.0 -4.742820    -5.611444        0.0   
2022-06-06 05:45:00                0.0 -4.672589    -5.841479        0.0   

                      rewards  
time                           
2022-01-01 00:00:00 -5.614021  
2022-01-01 00:15:00 -3.583872  
2022-01-01 00:30:00 -4.900382  
2022-01-01 00:45:00 -5.754368  
2022-01-01 01:00:00 -5.033976  
...                       ...  
2022-06-06 04:45:00 -5.563480  
2022-06-06 05:00:00 -5.939316  
2022-06-06 05:15:00 -5.675291  
2022-06-06 05:30:00 -5.611444  
2022-06-06 05:45:00 -5.841479  

[15000 rows x 13 columns]

In [40]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [41]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_VPP_Elvis_comparison()

In [43]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [44]:
env.plot_rewards_stats()

In [45]:
env.plot_EVs_kpi()

In [46]:
env.plot_load_kpi()

In [47]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [48]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-01 11:30:00, Parking_time: 23.78128929865366, Leaving_time: 2022-01-02 11:16:52.641475, SOC: 0.43625946628421053, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 18:00:00, Parking_time: 24, Leaving_time: 2023-01-01 18:00:00, SOC: 0.6216259570053639, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  9497.77 , over-consume=kWh  33046.69 , under-consume=kWh  23548.93 , Total_cost=€  506.18 , overcost=€  1378.4 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [49]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [50]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = MaskablePPO.load(MaskablePPO_path + model_id, env=env)

In [51]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, action_masks=action_masks, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8011.94 , over-consume=kWh  31802.45 , under-consume=kWh  23790.51 , Total_cost=€  453.41 , overcost=€  1322.95 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -17393.25 , over-consume=KWh  968.36 , under-consume=KWh  18361.61 , Total_cost=€  -602.26 , Overcost=€  40.89 
 EV_INFO: Av.EV_energy_leaving=kWh  66.28 , Std.EV_energy_leaving=kWh  21.25 , EV_departures =  1041 , EV_queue_left =  0
SCORE:  Cumulative_reward= 204121.06 - Step_rewars (load_t= 177470.33, EVs_energy_t= 14630.13)
 - Final_rewards (EVs_energy= 9040.4, Overconsume= -426.5, Underconsume= -10721.33, Overcost= 14128.02)
Episode:1 Score:204121.0624689354


In [52]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  84.344322  32.101665  92.209297  50.039749   
2022-06-06 05:00:00  84.344322  33.334782  93.442413  50.039749   
2022-06-06 05:15:00  84.344322  34.481468  94.589104  50.039749   
2022-06-06 05:30:00  84.094322  35.908463  96.016098  50.039749   
2022-06-06 05:45:00  83.844322  37.085060  97.192696  50.039749   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [0, 0, 0, 0]   
...                                       ...           ...   
2022-06-06 04:45:00  [9816, 9818, 9817, 9815]  [0, 1, 1, 0]   
2022-06-06 05:00:00  [9816, 9818, 9817, 9815]  [0, 1, 1, 0]   
2022-06-06 05:15:00  [9816, 9818, 9817, 9815]  [2, 1, 1, 0]   
2022-06-06 05:30:00  [9816, 9818, 9817, 9815]  [2, 1, 1, 0]   
2022-06-06 05:45:00  [9816, 9818, 9817, 9815]  [2, 1, 1, 0]   

                                     mask_truth  ev_charged_pwr  \
time                                                              
2022-01-01 00:00:00    [True, True, True, True]        0.000000   
2022-01-01 00:15:00    [True, True, True, True]        0.000000   
2022-01-01 00:30:00    [True, True, True, True]        0.000000   
2022-01-01 00:45:00    [True, True, True, True]        0.000000   
2022-01-01 01:00:00    [True, True, True, True]        0.000000   
...                                         ...             ...   
2022-06-06 04:45:00   [True, True, False, True]        6.851705   
2022-06-06 05:00:00   [True, True, False, True]        9.864917   
2022-06-06 05:15:00  [False, True, False, True]        9.173505   
2022-06-06 05:30:00  [False, True, False, True]       11.415941   
2022-06-06 05:45:00  [False, True, False, True]        9.412791   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.112733    -5.527135        0.0   
2022-01-01 00:15:00                0.0 -4.579849    -3.596173        0.0   
2022-01-01 00:30:00                0.0 -3.157704    -5.029387        0.0   
2022-01-01 00:45:00                0.0 -4.032326    -6.313520        0.0   
2022-01-01 01:00:00                0.0 -5.444872    -5.535803        0.0   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:00:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:15:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:30:00               -1.0  0.000000    15.000000        0.0   
2022-06-06 05:45:00               -1.0  0.000000    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -5.527135  
2022-01-01 00:15:00  -3.596173  
2022-01-01 00:30:00  -5.029387  
2022-01-01 00:45:00  -6.313520  
2022-01-01 01:00:00  -5.535803  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:45:00  15.000000  

[15000 rows x 13 columns]

In [54]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [56]:
env.plot_VPP_Elvis_comparison()

In [57]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [58]:
env.plot_rewards_stats()

In [59]:
env.plot_EVs_kpi()

In [60]:
env.plot_actions_kpi()

In [61]:
env.plot_load_kpi()

In [62]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [63]:
#env.close()